# Wavetable

A few experiments with the Wavetable crate.

First we need to do some setup to use Plotly for displaying graphs.

In [2]:
:dep rustfft = "5.0"
:dep plotly = { version = ">=0.6.0" }
:dep itertools-num = "0.1.3"

extern crate plotly;
extern crate rand_distr;
extern crate itertools_num;
extern crate itertools;

In [3]:
// Import 3rd party crates
// TODO: We probably don't need all of these, clean up
use itertools_num::linspace;
use plotly::{Bar, NamedColor, Plot, Rgb, Rgba, Scatter, Surface};
use plotly::common::{ColorScale, ColorScalePalette, DashType, Fill, Font, Line, LineShape, Marker, Mode, Side, Title};
use plotly::layout::{Axis, BarMode, GridPattern, Layout, LayoutGrid, Legend, RowOrder, TicksDirection};
use rand_distr::{Distribution, Normal, Uniform};
use rustfft::Fft;
use rustfft::FftPlanner;
use rustfft::num_complex::Complex;
use rustfft::num_traits::Zero;

use std::sync::Arc;

Then we load the Wavetable crate and create some handler objects.

In [4]:
:dep wavetable = { path = "/Users/ingo/Documents/Programming/src/rust/wavetable/" }

use wavetable::{Wavetable, WavetableRef, WtManager, WtReader, Harmonic, Float};

let mut wt_manager = WtManager::new(44100.0);
let basic_wave_id = 0;
wt_manager.add_basic_tables(basic_wave_id);

Define some helper functions for displaying the data.

In [5]:
// Add a simple linear trace to the given plot
fn add_trace(plot: &mut Plot, data: &Vec<f32>, num_values: usize, index: usize) {
    let t: Vec<f64> = linspace(0., num_values as f64, num_values).collect();
    let trace = Scatter::new(t, data.clone())
        .x_axis(&format!("x{}", index)).y_axis(&format!("y{}", index));
    plot.add_trace(trace);
}

// Add re and im component trace of complex number array to the given plot
fn add_trace_complex(plot: &mut Plot, data: &Vec<Complex<f32>>, num_values: usize, index: usize) {
    let t: Vec<f64> = linspace(0., num_values as f64, num_values).collect();
    let mut im: Vec<f32> = vec!();
    let mut re: Vec<f32> = vec!();
    for v in data {
        im.push(v.im);
        re.push(v.re);
    }
    let trace = Scatter::new(t.clone(), im).x_axis(&format!("x{}", index)).y_axis(&format!("y{}", index));
    plot.add_trace(trace);
    let trace = Scatter::new(t, re).x_axis(&format!("x{}", index)).y_axis(&format!("y{}", index));
    plot.add_trace(trace);
}

// Create a plot with a 2 x 2 grid layout
fn get_grid_plot() -> Plot {
    let mut plot = Plot::new();
    let layout = Layout::new().grid(LayoutGrid::new().rows(2).columns(2).pattern(GridPattern::Independent).x_gap(0.15).y_gap(0.15),);
    plot.set_layout(layout);
    plot
}

// Create a surface trace for all octave tables of a given waveshape
fn get_octave_plot(wt_ref: WavetableRef, table_id: usize) -> Box<Surface<f64, f64, f32>> {
    let wt = wt_ref.get_wave(table_id).clone();
    let t: Vec<f64> = linspace(0., wt_ref.num_samples as f64, wt_ref.num_samples).collect();
    let mut samples: Vec<Vec<f32>> = vec!(vec!(); wt_ref.num_octaves);
    for j in 0..wt_ref.num_octaves {
        samples[j].extend(&wt[(j * wt_ref.num_values)..(j * wt_ref.num_values + wt_ref.num_samples)]);
    }
    Surface::new(samples).x(t.clone()).y(t.clone())
}

// Create a surface trace for all waveshapes of a given wavetable
fn get_table_plot(wt_ref: WavetableRef) -> Box<Surface<f64, f64, f32>> {
    let t: Vec<f64> = linspace(0., wt_ref.num_samples as f64, wt_ref.num_samples).collect();
    let mut samples: Vec<Vec<f32>> = vec!(vec!(); wt_ref.num_samples);
    for i in 0..wt_ref.num_tables {
        let wt = wt_ref.get_wave(i).clone();
        samples[i].extend(&wt[0..wt_ref.num_samples]);
    }
    Surface::new(samples).x(t.clone()).y(t.clone())
}

// Create a plot, add a linear trace of the given data to it, and display it
fn show_trace_plot(data: &Vec<f32>, num_values: usize, index: usize) {
    let mut plot = Plot::new();
    add_trace(&mut plot, data, num_values, index);
    plot.notebook_display();
}

// Create a plot, add an octave trace to it, and display it
fn show_octave_plot(wt: WavetableRef, table_id: usize) {
    let mut plot = Plot::new();
    plot.add_trace(get_octave_plot(wt, table_id));
    plot.set_layout(Layout::new().height(600));
    plot.notebook_display();
}

// Create and show a Surface plot of all waveshapes in the given wavetable
fn show_table_plot(wt_ref: WavetableRef) {
    let mut plot = Plot::new();
    plot.add_trace(get_table_plot(wt_ref));
    plot.set_layout(Layout::new().height(600));
    plot.notebook_display();
}

## Examining the basic wave shapes

Create a plot of the basic wave shapes (sine, triangle, ramp, square)

In [6]:
let wt_basic = wt_manager.get_table(basic_wave_id).unwrap();
let mut plot = get_grid_plot();
for i in 0..wt_basic.num_tables {
    add_trace(&mut plot, wt_basic.get_wave(i), wt_basic.num_samples, i + 1);
}
plot.notebook_display();

Take the tables and run an FFT on them, show the first n of 1024 harmonics.

In [7]:
let harmonics = wt_basic.convert_to_harmonics();
let n = 50;
let mut plot = get_grid_plot();
for i in 0..wt_basic.num_tables {
    add_trace_complex(&mut plot, &harmonics[i], n, i + 1);
}
plot.notebook_display();

Creating 4 lists of harmonics with 2048 entries each for waves with 2048 samples


Show a surface plot of the bandlimited wave shapes. This shows the waveshape morphing from complex, with all harmonics, to increasingly simple waveforms by reducing the number of harmonics. Change table_id to any value between 0 and 3 to show other waveshapes.

In [8]:
let table_id = 3;
show_octave_plot(wt_basic, table_id);

# Convert wave to FFT and back

Let's load a simple wave table file and analyze it

In [9]:
let reader = WtReader::new("/Users/ingo/Documents/Programming/src/rust/wavetable");
let wt_akwf = reader.read_file("AKWF_0001.wav", Some(600)).unwrap();
show_trace_plot(wt_akwf.get_wave(0), wt_akwf.num_samples, 1);

Then run an FFT to get the list of harmonics.

In [10]:
let harmonics = wt_akwf.convert_to_harmonics();
let n = 600;
let mut plot = Plot::new();
add_trace_complex(&mut plot, &harmonics[0], n, 1);
plot.notebook_display();

Creating 1 lists of harmonics with 600 entries each for waves with 600 samples


We have two ways of generating the waveform back from the list of harmonics:

- Additive by stacking sine waves, which requires calculating magnitude and phase from the FFT result
- Running an inverse FFT

Currently Wavetable uses the inverse FFT.

In [11]:
let mut wt_akwf_new = Wavetable::new(1, 1, 600); // Reserve space for 1 waveshapes with 1 octave table
wt_akwf_new.insert_harmonics(&harmonics, 44100.0).unwrap();
show_trace_plot(wt_akwf_new.get_wave(0), wt_akwf_new.num_samples, 1);

Inserting harmonics into 1 tables, with 600 samples for 1 octaves


That does look close to the original shape. Now let's look at a surface plot of the bandlimited version.

In [12]:
let mut wt_akwf_bl = Wavetable::new(1, 11, 600); // Reserve space for 1 waveshapes with 11 octave tables
wt_akwf_bl.insert_harmonics(&harmonics, 44100.0).unwrap();
show_octave_plot(Arc::new(wt_akwf_bl), 0);

Inserting harmonics into 1 tables, with 600 samples for 11 octaves


# Load a complex wavetable and bandlimit it

Next we try bandlimitting a file that contains multiple waveforms. First we load the file. The graph below shows all 255 included waveforms as surface plot.

In [13]:
let reader = WtReader::new("/Users/ingo/Documents/Programming/src/rust/wavetable");
let wt_esw = reader.read_file("ESW Digital - Flavors.wav", Some(2048)).unwrap();
show_table_plot(wt_esw.clone());

Then bandlimit all the waveshapes and display the octave tables for one of the shapes as surface plot. This shows how the waveshape changes from a complex waveform to a single sine wave by reducing the number of harmonics. Change the value of "displayed_table_id" to any value between 0 and 255 to show a different waveform.

In [14]:
let displayed_table_id = 100;
let wt_bl = WtManager::bandlimit(wt_esw, 11, 44100.0);
show_octave_plot(wt_bl, displayed_table_id);

Creating 256 lists of harmonics with 2048 entries each for waves with 2048 samples
Inserting harmonics into 256 tables, with 2048 samples for 11 octaves
